In [1]:
import implicit

In [2]:
import pandas as pd
import numpy as np
from scipy.sparse import coo_matrix
import scipy
from scipy.sparse.linalg import svds
from numpy.linalg import svd 
from scipy.sparse import csr_matrix
import time
from sklearn import preprocessing
import matplotlib.pyplot as plt

In [3]:
def prepare_matrix(df):
    
    aggr1 = {
    'session_duration': 'max', 
    'video_duration': 'max'
    }
    
    train_s = df.groupby(['user_id', 'primary_video_id'])\
               .agg(aggr1).reset_index().reset_index()

    train_s['session_duration_clean'] = train_s[['session_duration', 'video_duration']].min(axis=1)
    train_s['watching_percentage'] = train_s['session_duration_clean']/train_s['video_duration']
    train_s = train_s[['user_id', 'primary_video_id', 'watching_percentage']]
    train_s = train_s[train_s['watching_percentage']>=0.5]
    
#     item_labels = preprocessing.LabelEncoder()
#     item_labels.fit(train_s.primary_video_id)
#     train_s['item_num'] = item_labels.transform(train_s.primary_video_id)

#     user_labels = preprocessing.LabelEncoder()
#     user_labels.fit(train_s.user_id)
#     train_s['user_num'] = user_labels.transform(train_s.user_id)

    user_labels = {k:v for v, k in dict(enumerate(train_s.user_id.unique())).items()}
    item_labels = {k:v for v, k in dict(enumerate(train_s.primary_video_id.unique())).items()}

    train_s['user_num'] = train_s['user_id'].map(user_labels)
    train_s['item_num'] = train_s['primary_video_id'].map(item_labels)

    row  = train_s['user_num'].values
    col  = train_s['item_num'].values
    data = train_s['watching_percentage'].values
#    matrix = csr_matrix(coo_matrix((data, (row, col)), shape=(len(user_mapper), len(item_mapper))))
    matrix = csr_matrix(coo_matrix((data, (row, col)), shape=(train_s['user_num'].nunique(), train_s['item_num'].nunique())))
    
    print(train.user_id.nunique(), train.primary_video_id.nunique(), matrix.shape)
  
    return matrix, item_labels, user_labels #item_mapper, user_mapper #

In [4]:
data_path = '/data/agoryach/datagym-recsys-01/big-hw-02/input/'

In [5]:
!ls -la $data_path

total 955772
drwxr-xr-x. 2 agoryach QAS UNIX USERS      4096 Jun  1 21:50 .
drwxr-xr-x. 4 agoryach QAS UNIX USERS        45 Jun  4 21:03 ..
-rw-r--r--. 1 agoryach QAS UNIX USERS  18254241 May 20 13:10 sample_submission.csv
-rw-r--r--. 1 agoryach QAS UNIX USERS  18189025 May 20 13:10 sample_submission_full.csv
-rw-r--r--. 1 agoryach QAS UNIX USERS 848273120 May 25 21:42 train_data_full.csv
-rw-r--r--. 1 agoryach QAS UNIX USERS         0 Jun  1 21:50 UsV_baseline.dat
-rw-r--r--. 1 agoryach QAS UNIX USERS   4610419 May 20 13:12 video_credits_data_full.csv
-rw-r--r--. 1 agoryach QAS UNIX USERS  45755815 May 20 13:12 video_favs_data_full.csv
-rw-r--r--. 1 agoryach QAS UNIX USERS    393658 May 20 13:13 video_genres_data_full.csv
-rw-r--r--. 1 agoryach QAS UNIX USERS  18125147 May 20 13:13 video_likes_data_full.csv
-rw-r--r--. 1 agoryach QAS UNIX USERS    349631 May 20 13:13 video_meta_data.csv
-rw-r--r--. 1 agoryach QAS UNIX USERS   7398795 May 20 13:13 video_meta_data_full.csv
-rw-r--r--. 1

In [6]:
train = pd.read_csv(data_path + 'train_data_full.csv')
test = pd.read_csv(data_path + 'sample_submission_full.csv')

In [7]:
train['session_start_datetime'] = pd.to_datetime(train['session_start_datetime'])
train['month'] = train['session_start_datetime'].apply(lambda x: x.month)
train['week'] = train['session_start_datetime'].apply(lambda x: x.week)

In [8]:
# film info
item_info = pd.read_csv(data_path + 'video_meta_data_full.csv')
# ohe по популярным актерам
credits = pd.read_csv(data_path + 'video_credits_data_full.csv')
# facts about favourite as flag
favs = pd.read_csv(data_path + 'video_favs_data_full.csv')
# facts about like as flag 0, 1, -1
likes = pd.read_csv(data_path + 'video_likes_data_full.csv')
# facts about orders
orders = pd.read_csv(data_path + 'video_orders_data_full.csv')

## prepare target

In [9]:
aggr1 = {
'session_duration': 'max', 
'video_duration': 'max',
'session_start_datetime':'max'
}

train_s = train.groupby(['user_id', 'primary_video_id', 'month', 'week'])\
           .agg(aggr1).reset_index().reset_index()

train_s['session_duration_clean'] = train_s[['session_duration', 'video_duration']].min(axis=1)
train_s['watching_percentage'] = train_s['session_duration_clean']/train_s['video_duration']
train_s = train_s[['user_id', 'primary_video_id', 'month', 'week', 'watching_percentage', 'session_start_datetime']]
train_s['target'] = np.where(train_s['watching_percentage']>=0.5, 1, 0)

In [10]:
train_s.target.value_counts()

1    3191622
0    1153869
Name: target, dtype: int64

In [11]:
train_s = train_s[['user_id', 'primary_video_id', 'week', 'month', 'target']]

## create features

### item features

In [12]:
item_info_agg = item_info.groupby('primary_video_id')\
.max().reset_index()\
[['primary_video_id', 'type', 'year', 'country', 'rating_imdb', 'rating_kinopoisk', \
  'score_by_popular', 'score_by_recommended', 'quality', 'age_limit']]

In [13]:
item_info_agg['item_FILM'] = np.where(item_info_agg['type']=='FILM', 1, 0)
item_info_agg['item_SERIAL'] = np.where(item_info_agg['type']=='SERIAL', 1, 0)
item_info_agg['item_SERIA'] = np.where(item_info_agg['type']=='SERIA', 1, 0)
item_info_agg['item_MULTFILM'] = np.where(item_info_agg['type']=='MULTFILM', 1, 0)
item_info_agg['item_SHOW'] = np.where((item_info_agg['type']=='SHOW')|(item_info_agg['type']=='SHOWFILM'), 1, 0)

item_info_agg['item_year_2000'] = np.where(item_info_agg['year'] >= 2000, 1, 0)
item_info_agg['item_year_1990'] = np.where((item_info_agg['year'] >= 1990)&(item_info_agg['year'] < 2000), 1, 0)
item_info_agg['item_year_1980'] = np.where((item_info_agg['year'] >= 1980)&(item_info_agg['year'] < 1990), 1, 0)
item_info_agg['item_year_1960'] = np.where((item_info_agg['year'] >= 1960)&(item_info_agg['year'] < 1980), 1, 0)
item_info_agg['item_year_1940'] = np.where((item_info_agg['year'] >= 1940)&(item_info_agg['year'] < 1960), 1, 0)
item_info_agg['item_year_1900'] = np.where((item_info_agg['year'] <  1940), 1, 0)

item_info_agg['country_USA'] = np.where((item_info_agg['country'] == 'США'), 1, 0)
item_info_agg['country_RUS'] = np.where((item_info_agg['country'] == 'Россия'), 1, 0)
item_info_agg['country_USSR'] = np.where((item_info_agg['country'] == 'СССР'), 1, 0)
item_info_agg['country_FRANCE'] = np.where((item_info_agg['country'] == 'Франция'), 1, 0)
item_info_agg['country_ENG'] = np.where((item_info_agg['country'] == 'Великобритания'), 1, 0)
item_info_agg['country_UKR'] = np.where((item_info_agg['country'] == 'Украина'), 1, 0)

item_info_agg['quality_FULL'] = np.where((item_info_agg['quality'] == 'FullHD'), 1, 0)
item_info_agg['quality_HD'] = np.where((item_info_agg['quality'] == 'HD'), 1, 0)

item_info_agg['age_limit_18'] = np.where(item_info_agg['age_limit']==18, 1, 0)
item_info_agg['age_limit_16'] = np.where(item_info_agg['age_limit']==16, 1, 0)
item_info_agg['age_limit_12'] = np.where(item_info_agg['age_limit']==12, 1, 0)
item_info_agg['age_limit_6']  = np.where(item_info_agg['age_limit']==6, 1, 0)

In [14]:
item_info_agg.drop(['type', 'year', 'country', 'quality', 'age_limit'], axis=1, inplace=True)

In [15]:
top10_actors = credits[credits['type']=='ROLE'].title.value_counts().head(10).index
top10_directors = credits[credits['type']=='DIRECTOR'].title.value_counts().head(10).index
top10_scenario = credits[credits['type']=='SCENARIO'].title.value_counts().head(10).index

top30_actors = credits[credits['type']=='ROLE'].title.value_counts().head(30).index
top30_directors = credits[credits['type']=='DIRECTOR'].title.value_counts().head(30).index
top30_scenario = credits[credits['type']=='SCENARIO'].title.value_counts().head(30).index

top100_actors = credits[credits['type']=='ROLE'].title.value_counts().head(100).index
top100_directors = credits[credits['type']=='DIRECTOR'].title.value_counts().head(100).index
top100_scenario = credits[credits['type']=='SCENARIO'].title.value_counts().head(100).index

In [16]:
credits['top10_actors'] = np.where(credits.title.isin(top10_actors), 1, 0)
credits['top10_directors'] = np.where(credits.title.isin(top10_directors), 1, 0)
credits['top10_scenario'] = np.where(credits.title.isin(top10_scenario), 1, 0)

credits['top30_actors'] = np.where(credits.title.isin(top30_actors), 1, 0)
credits['top30_directors'] = np.where(credits.title.isin(top30_directors), 1, 0)
credits['top30_scenario'] = np.where(credits.title.isin(top30_scenario), 1, 0)

credits['top100_actors'] = np.where(credits.title.isin(top100_actors), 1, 0)
credits['top100_directors'] = np.where(credits.title.isin(top100_directors), 1, 0)
credits['top100_scenario'] = np.where(credits.title.isin(top100_scenario), 1, 0)

credits_agg = credits.groupby('primary_video_id').sum().reset_index()
item_info_agg = item_info_agg.merge(credits_agg, how='left').fillna(-1)

In [17]:
favs['created_at'] = pd.to_datetime(favs['created_at'])
favs['week'] = favs['created_at'].apply(lambda x: x.week)
favs['is_fav'] = [1]*favs.shape[0]

favs_agg = favs.groupby(['primary_video_id', 'week']).sum()[['is_fav']]\
.reset_index().rename(columns={'is_fav':'is_fav_sum'})

favs_agg['is_fav_cumsum'] = favs_agg\
.sort_values(['primary_video_id', 'week'], ascending=[True, True])\
.groupby(['primary_video_id']).cumsum().is_fav_sum

In [18]:
likes['created_at'] = pd.to_datetime(likes['created_at'])
likes['week'] = likes['created_at'].apply(lambda x: x.week)
likes['is_disliked'] = np.where(likes['is_liked']==0, 1, 0)

likes_agg = likes.groupby(['primary_video_id', 'week']).sum()[['is_liked', 'is_disliked']]\
.reset_index().rename(columns={'is_liked':'is_like_sum', 'is_disliked':'is_disliked_sum'})

likes_agg['is_like_cumsum'] = likes_agg\
.sort_values(['primary_video_id', 'week'], ascending=[True, True])\
.groupby(['primary_video_id']).cumsum().is_like_sum

likes_agg['is_disliked_cumsum'] = likes_agg\
.sort_values(['primary_video_id', 'week'], ascending=[True, True])\
.groupby(['primary_video_id']).cumsum().is_disliked_sum

likes_agg['like_prc'] = likes_agg['is_like_cumsum']/(likes_agg['is_like_cumsum'] + likes_agg['is_disliked_cumsum'])

In [19]:
orders['created_at'] = pd.to_datetime(orders['created_at'])
orders['week'] = orders['created_at'].apply(lambda x: x.week)
orders['is_order'] = [1]*orders.shape[0]

orders_agg = orders.groupby(['primary_video_id', 'week']).sum()[['is_order']]\
.reset_index().rename(columns={'is_order':'is_order_sum'})

orders_agg['is_order_cumsum'] = orders_agg\
.sort_values(['primary_video_id', 'week'], ascending=[True, True])\
.groupby(['primary_video_id']).cumsum().is_order_sum

### user features

In [20]:
train = train.sort_values('session_start_datetime')
train['user_items_cnt'] = train.groupby('user_id').cumcount() + 1
train['session_duration_cumsum'] = train.groupby('user_id').cumsum()['session_duration']
train['player_position_min_cumsum'] = train.groupby('user_id').cumsum()['player_position_min']
train['player_position_max_cumsum'] = train.groupby('user_id').cumsum()['player_position_max']
train['watching_percentage_cumsum'] = train.groupby('user_id').cumsum()['watching_percentage']

train['session_duration_mean'] = train['session_duration_cumsum']/train['user_items_cnt']
train['player_position_min_mean'] = train['player_position_min_cumsum']/train['user_items_cnt']
train['player_position_max_mean'] = train['player_position_max_cumsum']/train['user_items_cnt']
train['watching_percentage_mean'] = train['watching_percentage_cumsum']/train['user_items_cnt']

In [21]:
user_info_agg = train.groupby(['user_id', 'week']).mean()\
[['session_duration_mean', 'player_position_min_mean', 'player_position_max_mean', 'watching_percentage_mean']]\
.reset_index()

### join target with feats

In [179]:
# item_info_agg - фичи про item без привязки ко времени
# favs_agg, likes_agg, orders_agg - фичи про item, но с привязкой к неделе
# user_info_agg - фичи про user с привязкой к неделе

In [22]:
train_s.shape

(4345491, 5)

In [23]:
train_s = train_s.merge(item_info_agg, how='left', on='primary_video_id')

In [24]:
train_s.shape

(4345491, 41)

In [25]:
tmp = train_s.merge(favs_agg[['primary_video_id', 'week', 'is_fav_cumsum']], how='left', on=['primary_video_id'])
tmp = tmp[tmp['week_y'] < tmp['week_x']]
tmp['week_diff'] = tmp['week_x'] - tmp['week_y']
fav_clean = tmp.groupby(['user_id', 'primary_video_id', 'week_x']).min()[['week_diff']].reset_index()
tmp = tmp.merge(fav_clean)[['user_id', 'primary_video_id', 'week_x', 'is_fav_cumsum']]
tmp = tmp.rename(columns={'week_x': 'week'})
train_s = train_s.merge(tmp, how='left', on=['user_id', 'primary_video_id', 'week']).fillna(-1)

In [26]:
train_s.shape, train_s.drop_duplicates().shape

((4389461, 42), (4345491, 42))

In [27]:
train_s = train_s.drop_duplicates()

In [28]:
tmp = train_s.merge(likes_agg[['primary_video_id', 'week', 'is_like_cumsum', 'is_disliked_cumsum', 'like_prc']], 
                    how='left', on=['primary_video_id'])
tmp = tmp[tmp['week_y'] < tmp['week_x']]
tmp['week_diff'] = tmp['week_x'] - tmp['week_y']
fav_clean = tmp.groupby(['user_id', 'primary_video_id', 'week_x']).min()[['week_diff']].reset_index()
tmp = tmp.merge(fav_clean)[['user_id', 'primary_video_id', 'week_x',  'is_like_cumsum', 'is_disliked_cumsum', 'like_prc']]
tmp = tmp.rename(columns={'week_x': 'week'})
train_s = train_s.merge(tmp, how='left', on=['user_id', 'primary_video_id', 'week']).fillna(-1)

In [29]:
train_s.shape, train_s.drop_duplicates().shape

((4389409, 45), (4345491, 45))

In [30]:
train_s = train_s.drop_duplicates()

In [31]:
tmp = train_s.merge(orders_agg[['primary_video_id', 'week', 'is_order_cumsum']], 
                    how='left', on=['primary_video_id'])
tmp = tmp[tmp['week_y'] < tmp['week_x']]
tmp['week_diff'] = tmp['week_x'] - tmp['week_y']
fav_clean = tmp.groupby(['user_id', 'primary_video_id', 'week_x']).min()[['week_diff']].reset_index()
tmp = tmp.merge(fav_clean)[['user_id', 'primary_video_id', 'week_x',  'is_order_cumsum']]
tmp = tmp.rename(columns={'week_x': 'week'})
train_s = train_s.merge(tmp, how='left', on=['user_id', 'primary_video_id', 'week']).fillna(-1)

In [32]:
train_s.shape, train_s.drop_duplicates().shape

((4370753, 46), (4345491, 46))

In [33]:
train_s = train_s.drop_duplicates()

In [34]:
tmp = train_s.merge(user_info_agg[['user_id', 'week', 'session_duration_mean', 'player_position_min_mean', 
                                   'player_position_max_mean', 'watching_percentage_mean']], 
                    how='left', on=['user_id'])
tmp = tmp[tmp['week_y'] < tmp['week_x']]
tmp['week_diff'] = tmp['week_x'] - tmp['week_y']
fav_clean = tmp.groupby(['user_id', 'primary_video_id', 'week_x']).min()[['week_diff']].reset_index()
tmp = tmp.merge(fav_clean)[['user_id', 'primary_video_id', 'week_x',  'session_duration_mean', 'player_position_min_mean', 'player_position_max_mean', 'watching_percentage_mean']]
tmp = tmp.rename(columns={'week_x': 'week'})
train_s = train_s.merge(tmp, how='left', on=['user_id', 'primary_video_id', 'week']).fillna(-1)

In [35]:
train_s.shape, train_s.drop_duplicates().shape

((4384021, 50), (4345491, 50))

In [36]:
train_s = train_s.drop_duplicates()

### secondary hist feats

In [37]:
train_s = train_s.sort_values(['user_id', 'week'])

In [38]:
train_s['user_row_num'] = train_s.groupby('user_id').cumcount() + 1

In [39]:
train_s['rating_imdb_cumsum'] = train_s.groupby('user_id').cumsum()['rating_imdb']
train_s['rating_kinopoisk_cumsum'] = train_s.groupby('user_id').cumsum()['rating_kinopoisk']
train_s['score_by_popular_cumsum'] = train_s.groupby('user_id').cumsum()['score_by_popular']
train_s['score_by_recommended_cumsum'] = train_s.groupby('user_id').cumsum()['score_by_recommended']

train_s['rating_imdb_mean'] = train_s['rating_imdb_cumsum']/train_s['user_row_num']
train_s['rating_kinopoisk_mean'] = train_s['rating_kinopoisk_cumsum']/train_s['user_row_num']
train_s['score_by_popular_mean'] = train_s['score_by_popular_cumsum']/train_s['user_row_num']
train_s['score_by_recommended_mean'] = train_s['score_by_recommended_cumsum']/train_s['user_row_num']

train_s.drop(['rating_imdb_cumsum', 'rating_kinopoisk_cumsum', 'score_by_popular_cumsum', 'score_by_recommended_cumsum'],
             axis=1, inplace=True)

In [40]:
train_s['rating_imdb_mean_shift'] = train_s['rating_imdb_mean'].shift(1)
train_s['rating_imdb_mean_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['rating_imdb_mean_shift'])

train_s['rating_kinopoisk_mean_shift'] = train_s['rating_kinopoisk_mean'].shift(1)
train_s['rating_kinopoisk_mean_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['rating_kinopoisk_mean'])

train_s['score_by_popular_mean_shift'] = train_s['score_by_popular_mean'].shift(1)
train_s['score_by_popular_mean_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['score_by_popular_mean_shift'])

train_s['score_by_recommended_mean_shift'] = train_s['score_by_recommended_mean'].shift(1)
train_s['score_by_recommended_mean_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['score_by_recommended_mean_shift'])

In [41]:
train_s['item_FILM_cumsum']      = train_s.groupby('user_id').cumsum()['item_FILM']
train_s['item_SERIAL_cumsum']    = train_s.groupby('user_id').cumsum()['item_SERIAL']
train_s['item_SERIA_cumsum']     = train_s.groupby('user_id').cumsum()['item_SERIA']
train_s['item_MULTFILM_cumsum']  = train_s.groupby('user_id').cumsum()['item_MULTFILM']
train_s['item_SHOW_cumsum']      = train_s.groupby('user_id').cumsum()['item_SHOW']
train_s['item_year_2000_cumsum'] = train_s.groupby('user_id').cumsum()['item_year_2000']
train_s['item_year_1990_cumsum'] = train_s.groupby('user_id').cumsum()['item_year_1990']
train_s['item_year_1980_cumsum'] = train_s.groupby('user_id').cumsum()['item_year_1980']
train_s['item_year_1960_cumsum'] = train_s.groupby('user_id').cumsum()['item_year_1960']
train_s['item_year_1940_cumsum'] = train_s.groupby('user_id').cumsum()['item_year_1940']
train_s['item_year_1900_cumsum'] = train_s.groupby('user_id').cumsum()['item_year_1900']

train_s['country_USA_cumsum']    = train_s.groupby('user_id').cumsum()['country_USA']
train_s['country_RUS_cumsum']    = train_s.groupby('user_id').cumsum()['country_RUS']
train_s['country_USSR_cumsum']   = train_s.groupby('user_id').cumsum()['country_USSR']
train_s['country_FRANCE_cumsum'] = train_s.groupby('user_id').cumsum()['country_FRANCE']
train_s['country_ENG_cumsum']    = train_s.groupby('user_id').cumsum()['country_ENG']
train_s['country_UKR_cumsum']    = train_s.groupby('user_id').cumsum()['country_UKR']
train_s['quality_FULL_cumsum']   = train_s.groupby('user_id').cumsum()['quality_FULL']
train_s['quality_HD_cumsum']     = train_s.groupby('user_id').cumsum()['quality_HD']

train_s['top10_actors_cumsum']     = train_s.groupby('user_id').cumsum()['top10_actors']
train_s['top30_actors_cumsum']     = train_s.groupby('user_id').cumsum()['top30_actors']
train_s['top100_actors_cumsum']    = train_s.groupby('user_id').cumsum()['top100_actors']
train_s['top10_directors_cumsum']  = train_s.groupby('user_id').cumsum()['top10_directors']
train_s['top30_directors_cumsum']  = train_s.groupby('user_id').cumsum()['top30_directors']
train_s['top100_directors_cumsum'] = train_s.groupby('user_id').cumsum()['top100_directors']
train_s['top10_scenario_cumsum']   = train_s.groupby('user_id').cumsum()['top10_scenario']
train_s['top30_scenario_cumsum']   = train_s.groupby('user_id').cumsum()['top30_scenario']
train_s['top100_scenario_cumsum']  = train_s.groupby('user_id').cumsum()['top100_scenario']

train_s['age_limit_18_cumsum'] = train_s.groupby('user_id').cumsum()['age_limit_18']
train_s['age_limit_16_cumsum'] = train_s.groupby('user_id').cumsum()['age_limit_16']
train_s['age_limit_12_cumsum'] = train_s.groupby('user_id').cumsum()['age_limit_12']
train_s['age_limit_6_cumsum']  = train_s.groupby('user_id').cumsum()['age_limit_6']

In [42]:
train_s['item_FILM_cumsum_shift']      = train_s['item_FILM_cumsum'].shift(1)    
train_s['item_SERIAL_cumsum_shift']    = train_s['item_SERIAL_cumsum'].shift(1)   
train_s['item_SERIA_cumsum_shift']     = train_s['item_SERIA_cumsum'].shift(1)     
train_s['item_MULTFILM_cumsum_shift']  = train_s['item_MULTFILM_cumsum'].shift(1)  
train_s['item_SHOW_cumsum_shift']      = train_s['item_SHOW_cumsum'].shift(1)      
train_s['item_year_2000_cumsum_shift'] = train_s['item_year_2000_cumsum'].shift(1) 
train_s['item_year_1990_cumsum_shift'] = train_s['item_year_1990_cumsum'].shift(1) 
train_s['item_year_1980_cumsum_shift'] = train_s['item_year_1980_cumsum'].shift(1) 
train_s['item_year_1960_cumsum_shift'] = train_s['item_year_1960_cumsum'].shift(1) 
train_s['item_year_1940_cumsum_shift'] = train_s['item_year_1940_cumsum'].shift(1) 
train_s['item_year_1900_cumsum_shift'] = train_s['item_year_1900_cumsum'].shift(1) 

train_s['country_USA_cumsum_shift']    = train_s['country_USA_cumsum'].shift(1)    
train_s['country_RUS_cumsum_shift']    = train_s['country_RUS_cumsum'].shift(1)    
train_s['country_USSR_cumsum_shift']   = train_s['country_USSR_cumsum'].shift(1)   
train_s['country_FRANCE_cumsum_shift'] = train_s['country_FRANCE_cumsum'].shift(1) 
train_s['country_ENG_cumsum_shift']    = train_s['country_ENG_cumsum'].shift(1)    
train_s['country_UKR_cumsum_shift']    = train_s['country_UKR_cumsum'].shift(1)    
train_s['quality_FULL_cumsum_shift']   = train_s['quality_FULL_cumsum'].shift(1)   
train_s['quality_HD_cumsum_shift']     = train_s['quality_HD_cumsum'].shift(1)     

train_s['top10_actors_cumsum_shift']     = train_s['top10_actors_cumsum'].shift(1)      
train_s['top30_actors_cumsum_shift']     = train_s['top30_actors_cumsum'].shift(1)      
train_s['top100_actors_cumsum_shift']    = train_s['top100_actors_cumsum'].shift(1)     
train_s['top10_directors_cumsum_shift']  = train_s['top10_directors_cumsum'].shift(1)   
train_s['top30_directors_cumsum_shift']  = train_s['top30_directors_cumsum'].shift(1)   
train_s['top100_directors_cumsum_shift'] = train_s['top100_directors_cumsum'].shift(1)  
train_s['top10_scenario_cumsum_shift']   = train_s['top10_scenario_cumsum'].shift(1)    
train_s['top30_scenario_cumsum_shift']   = train_s['top30_scenario_cumsum'].shift(1)    
train_s['top100_scenario_cumsum_shift']  = train_s['top100_scenario_cumsum'].shift(1)  

train_s['age_limit_18_cumsum_shift'] = train_s['age_limit_18_cumsum'].shift(1)    
train_s['age_limit_16_cumsum_shift'] = train_s['age_limit_16_cumsum'].shift(1)   
train_s['age_limit_12_cumsum_shift'] = train_s['age_limit_12_cumsum'].shift(1)     
train_s['age_limit_6_cumsum_shift']  = train_s['age_limit_6_cumsum'].shift(1)  

In [43]:
train_s['item_FILM_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['item_FILM_cumsum_shift'])
train_s['item_SERIAL_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['item_FILM_cumsum_shift'])
train_s['item_SERIA_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['item_SERIA_cumsum_shift'])
train_s['item_MULTFILM_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['item_MULTFILM_cumsum_shift'])
train_s['item_SHOW_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['item_SHOW_cumsum_shift'])
train_s['item_year_2000_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['item_year_2000_cumsum_shift'])
train_s['item_year_1990_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['item_year_1990_cumsum_shift'])
train_s['item_year_1980_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['item_year_1980_cumsum_shift'])
train_s['item_year_1960_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['item_year_1960_cumsum_shift'])
train_s['item_year_1940_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['item_year_1940_cumsum_shift'])
train_s['item_year_1900_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['item_year_1900_cumsum_shift'])
train_s['country_USA_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['country_USA_cumsum_shift'])
train_s['country_RUS_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['country_RUS_cumsum_shift'])
train_s['country_USSR_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['country_USSR_cumsum_shift'])
train_s['country_FRANCE_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['country_FRANCE_cumsum_shift'])

train_s['country_ENG_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['country_ENG_cumsum_shift'])
train_s['country_UKR_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['country_UKR_cumsum_shift'])
train_s['quality_FULL_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['quality_FULL_cumsum_shift'])
train_s['quality_HD_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['quality_HD_cumsum_shift'])
train_s['top10_actors_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['top10_actors_cumsum_shift'])
train_s['top30_actors_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['top30_actors_cumsum_shift'])
train_s['top100_actors_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['top100_actors_cumsum_shift'])
train_s['top10_directors_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['top10_directors_cumsum_shift'])
train_s['top30_directors_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['top30_directors_cumsum_shift'])
train_s['top100_directors_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['top100_directors_cumsum_shift'])
train_s['top10_scenario_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['top10_scenario_cumsum_shift'])
train_s['top30_scenario_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['top30_scenario_cumsum_shift'])
train_s['top100_scenario_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['top100_scenario_cumsum_shift'])

train_s['age_limit_18_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['age_limit_18_cumsum_shift'])
train_s['age_limit_16_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['age_limit_16_cumsum_shift'])
train_s['age_limit_12_cumsum_shift'] = np.where(train_s['user_row_num'] == 1, 0, train_s['age_limit_12_cumsum_shift'])
train_s['age_limit_6_cumsum_shift']  = np.where(train_s['user_row_num'] == 1, 0, train_s['age_limit_6_cumsum_shift'])

## fit

In [223]:
item_info_agg_cols = ['rating_imdb', 'rating_kinopoisk', 'score_by_popular', 'score_by_recommended', 
                      'item_FILM', 'item_SERIAL', 'item_SERIA', 'item_MULTFILM', 'item_SHOW',
                      'item_year_2000', 'item_year_1990', 'item_year_1980', 'item_year_1960', 'item_year_1940',
                      'item_year_1900', 'country_USA', 'country_RUS', 'country_USSR', 'country_FRANCE', 
                      'country_ENG', 'country_UKR', 'quality_FULL', 'quality_HD', 'top30_actors', 
                      'top30_directors','top30_scenario', 'top10_actors', 'top10_directors', 'top10_scenario', 
                      'top100_actors', 'top100_directors', 'top100_scenario', 'age_limit_18', 'age_limit_16', 
                      'age_limit_12', 'age_limit_6']

action_cols = ['is_fav_cumsum', 'is_like_cumsum', 'is_disliked_cumsum', 'like_prc', 'is_order_cumsum']
user_cols = ['session_duration_mean', 'player_position_min_mean', 'player_position_max_mean', 'watching_percentage_mean']

add_feats = ['user_row_num', 'rating_imdb_mean_shift', 'rating_kinopoisk_mean_shift', 
             'score_by_popular_mean_shift', 'score_by_recommended_mean_shift',
            'item_FILM_cumsum_shift','item_SERIAL_cumsum_shift', 'item_SERIA_cumsum_shift', 'item_MULTFILM_cumsum_shift',
            'item_SHOW_cumsum_shift', 'item_year_2000_cumsum_shift', 'item_year_1990_cumsum_shift', 
            'item_year_1980_cumsum_shift', 'item_year_1960_cumsum_shift', 'item_year_1940_cumsum_shift', 
            'item_year_1900_cumsum_shift', 'country_USA_cumsum_shift', 'country_RUS_cumsum_shift', 'country_USSR_cumsum_shift',
            'country_FRANCE_cumsum_shift', 'country_ENG_cumsum_shift', 'country_UKR_cumsum_shift', 'quality_FULL_cumsum_shift',
            'quality_HD_cumsum_shift', 'top10_actors_cumsum_shift', 'top30_actors_cumsum_shift', 'top100_actors_cumsum_shift', 
            'top10_directors_cumsum_shift', 'top30_directors_cumsum_shift', 'top100_directors_cumsum_shift', 'top10_scenario_cumsum_shift',
            'top30_scenario_cumsum_shift', 'top100_scenario_cumsum_shift', 'age_limit_18_cumsum_shift', 'age_limit_16_cumsum_shift', 
            'age_limit_12_cumsum_shift', 'age_limit_6_cumsum_shift']

train_feats = item_info_agg_cols + action_cols + user_cols + add_feats

In [226]:
train_s[train_feats].isna().sum().sum()

0

In [225]:
train_ss = train_s[train_feats + ['user_id', 'primary_video_id', 'target', 'month']]

In [47]:
train_df = train_ss[train_ss['month'] != 9]
test_df  = train_ss[train_ss['month'] == 9]

In [48]:
train_df.shape, test_df.shape

((2923774, 86), (1421717, 86))

In [49]:
from sklearn.ensemble import RandomForestClassifier

In [197]:
rf = RandomForestClassifier(n_estimators=200, n_jobs=-1, random_state=11)

In [198]:
rf.fit(train_df[train_feats].values, train_df.target.values)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=200,
                       n_jobs=-1, oob_score=False, random_state=11, verbose=0,
                       warm_start=False)

In [208]:
train_ss[train_feats].shape

(4345491, 84)

In [207]:
set(train_df[train_feats].columns) - set(new_feats)

set()

In [52]:
prob = rf.predict_proba(test_df[train_feats].values)[:, 1]

In [53]:
from sklearn.metrics import roc_auc_score

In [54]:
roc_auc_score(test_df.target.values, prob)

0.7118738420059452

In [104]:
def map_at_k(df, k):
    df = df[df['rnk'] < k]
    df['target_cumsum'] = df[['user_id', 'target']].groupby('user_id').cumsum()
    df['for_running_sum'] = df['target_cumsum']/(df['rnk']+1)
    agg_df = df[df['target']==1][['user_id', 'for_running_sum']].groupby('user_id').mean().reset_index()
    agg_df.columns = ['user_id', 'ap']
    return agg_df['ap'].mean()

## predict

In [55]:
test = pd.read_csv(data_path + 'sample_submission_full.csv').drop('primary_video_id', axis=1)

In [56]:
hot_users = set(test['user_id'].unique())&(set(train_ss['user_id'].unique()))
cold_users = set(test['user_id'].unique())-(set(train_ss['user_id'].unique()))

### cold start

In [57]:
matrix, item_labels, user_labels = prepare_matrix(train.copy())

407381 5266 (397294, 5255)


In [58]:
# recs for cold users

# самые популярные товары
item_pop_matrix = pd.DataFrame([])
item_pop_matrix['item_id'] = item_labels.keys()
item_pop_matrix['cnt_not_null'] = (matrix.T > 0).sum(axis=1)

# среднее по товарам
(x,y,z) = scipy.sparse.find(matrix)
countings = np.bincount(y)
sums = np.bincount(y, weights=z)
averages = sums/countings

item_pop_matrix['item_means'] = averages

In [59]:
n_item_count = 8000

top10_items = item_pop_matrix[item_pop_matrix['cnt_not_null'] > n_item_count]\
.sort_values('item_means', ascending=False)\
.head(10)['item_id'].values

len(top10_items), item_info[item_info['primary_video_id'].isin(top10_items)].title.unique()

(10, array(['Суперкрылья. Джетт и его друзья', 'МиниФорс',
        'Паровозики из Чаггингтона', 'Фиксики', 'Трое из Простоквашино',
        'Школа', 'Маша и Медведь', 'Октонавты', 'Приключения Тайо',
        'Я худею'], dtype=object))

In [60]:
result2 = pd.DataFrame(cold_users, columns=['user_id'])
result2['primary_video_id'] = ' '.join([str(x) for x in top10_items])

In [61]:
item_pop_matrix[item_pop_matrix.cnt_not_null >= 100].shape

(3159, 3)

In [62]:
# hyperparam - 0.9
item_pop_matrix[(item_pop_matrix.cnt_not_null >= 100)&(item_pop_matrix.item_means >= 0.9)].shape

(1817, 3)

In [63]:
154522*1817

280766474

### hot users

In [64]:
import warnings
warnings.filterwarnings("ignore")

In [67]:
pop_count = 100
pop_prc = 0.9

pop_films = item_pop_matrix[(item_pop_matrix.cnt_not_null >= pop_count)&
                            (item_pop_matrix.item_means >= pop_prc)].item_id.unique()

In [68]:
#hot_test = test[test['user_id'].isin(hot_users)]
# hot_test['primary_video_id_list'] = pd.Series([pop_films]*hot_test.shape[0])
# hot_test.shape
# full_hot_test = hot_test.set_index('user_id').primary_video_id_list.explode().reset_index()\
# .rename(columns={'primary_video_id_list':'primary_video_id'})
# full_hot_test = full_hot_test.merge(train_s[['user_id', 'primary_video_id', 'week']], 
#                                     how='left', on=['user_id', 'primary_video_id'])
# full_hot_test.shape
# full_hot_test = full_hot_test[full_hot_test['week'].isna()]
# full_hot_test.shape
# full_hot_test.drop('week', axis=1, inplace=True)

### prepare feats

In [232]:
max_fav_week = favs_agg[['primary_video_id', 'week']].groupby('primary_video_id').max()[['week']].reset_index()
favs_agg_test = favs_agg.merge(max_fav_week)

max_like_week = likes_agg[['primary_video_id', 'week']].groupby('primary_video_id').max()[['week']].reset_index()
likes_agg_test = likes_agg.merge(max_like_week)

max_order_week = orders_agg[['primary_video_id', 'week']].groupby('primary_video_id').max()[['week']].reset_index()
orders_agg_test = orders_agg.merge(max_order_week)



In [233]:
item_info_final = item_info_agg.merge(favs_agg_test[['primary_video_id', 'is_fav_cumsum']], 
                                      how='left', on='primary_video_id').fillna(-1)\
                               .merge(likes_agg_test[['primary_video_id', 'is_like_cumsum', 'is_disliked_cumsum', 'like_prc']], 
                                      how='left', on='primary_video_id').fillna(-1)\
                               .merge(orders_agg_test[['primary_video_id', 'is_order_cumsum']], 
                                      how='left', on='primary_video_id').fillna(-1)

In [234]:
max_user_week = user_info_agg[['user_id', 'week']].groupby('user_id').max()[['week']].reset_index()
user_agg_test = user_info_agg.merge(max_user_week)

user_cum_feats = ['item_FILM_cumsum', 'item_SERIAL_cumsum', 'item_SERIA_cumsum', 'item_MULTFILM_cumsum', 'item_SHOW_cumsum',
                  'item_year_2000_cumsum', 'item_year_1990_cumsum', 'item_year_1980_cumsum', 'item_year_1960_cumsum',
                  'item_year_1940_cumsum', 'item_year_1900_cumsum', 'country_USA_cumsum', 'country_RUS_cumsum', 
                  'country_USSR_cumsum', 'country_FRANCE_cumsum', 'country_ENG_cumsum', 'country_UKR_cumsum',
                  'quality_FULL_cumsum', 'quality_HD_cumsum', 'top10_actors_cumsum', 'top30_actors_cumsum',
                  'top100_actors_cumsum', 'top10_directors_cumsum', 'top30_directors_cumsum', 'top100_directors_cumsum',
                  'top10_scenario_cumsum', 'top30_scenario_cumsum', 'top100_scenario_cumsum', 'age_limit_18_cumsum',
                  'age_limit_16_cumsum', 'age_limit_12_cumsum', 'age_limit_6_cumsum', 'user_row_num',
                  'rating_imdb_mean', 'rating_kinopoisk_mean', 'score_by_popular_mean', 'score_by_recommended_mean'
                 ]

train_s['rnk'] = train_s.groupby('user_id').cumcount()
max_user_cum_week = train_s[['user_id', 'rnk']].groupby('user_id').max()[['rnk']].reset_index()
user_cum_agg_test = train_s[['user_id', 'rnk']+user_cum_feats].merge(max_user_cum_week, on=['user_id', 'rnk'])

In [235]:
user_cum_agg_test.shape, user_agg_test.shape

((407381, 39), (407381, 6))

In [236]:
user_info_final = user_cum_agg_test.merge(user_agg_test, on=['user_id'], how='left').drop('week', axis=1)

In [237]:
for_rename = ['item_FILM_cumsum', 'item_SERIAL_cumsum', 'item_SERIA_cumsum', 'item_MULTFILM_cumsum', 'item_SHOW_cumsum',
                  'item_year_2000_cumsum', 'item_year_1990_cumsum', 'item_year_1980_cumsum', 'item_year_1960_cumsum',
                  'item_year_1940_cumsum', 'item_year_1900_cumsum', 'country_USA_cumsum', 'country_RUS_cumsum', 
                  'country_USSR_cumsum', 'country_FRANCE_cumsum', 'country_ENG_cumsum', 'country_UKR_cumsum',
                  'quality_FULL_cumsum', 'quality_HD_cumsum', 'top10_actors_cumsum', 'top30_actors_cumsum',
                  'top100_actors_cumsum', 'top10_directors_cumsum', 'top30_directors_cumsum', 'top100_directors_cumsum',
                  'top10_scenario_cumsum', 'top30_scenario_cumsum', 'top100_scenario_cumsum', 'age_limit_18_cumsum',
                  'age_limit_16_cumsum', 'age_limit_12_cumsum', 'age_limit_6_cumsum',
                  'rating_imdb_mean', 'rating_kinopoisk_mean', 'score_by_popular_mean', 'score_by_recommended_mean'
                 ] 

renamed = []
for col in for_rename:
    renamed.append(col + '_shift')

In [238]:
renamer = {k:v for k,v in zip(for_rename, renamed)}

In [239]:
user_info_final = user_info_final.rename(columns=renamer)

### check

In [133]:
set(item_info_agg_cols) - set(item_info_final)

set()

In [134]:
set(action_cols) - set(item_info_final)

set()

In [135]:
set(user_cols) - set(user_info_final)

set()

In [151]:
set(add_feats) - set(user_info_final)

set()

### join feats

In [154]:
# full_hot_test = full_hot_test.merge(item_info_final, on='primary_video_id')
# user_info_final.drop('rnk', axis=1, inplace=True)
# full_hot_test = full_hot_test.merge(user_info_final, on='user_id')
# full_hot_test.head()
# del full_hot_test

In [240]:
item_mapper = {v:k for k, v in enumerate(item_info_final.primary_video_id.unique())}
user_mapper = {v:k for k, v in enumerate(train.user_id.unique())}

In [250]:
item_mapper_rev = {v:k for k,v in item_mapper.items()}
user_mapper_rev = {v:k for k,v in user_mapper.items()}

In [241]:
item_info_final['item_num'] = item_info_final['primary_video_id'].map(item_mapper).astype(int)
item_info_final.drop('primary_video_id', axis=1, inplace=True)

user_info_final['user_num'] = user_info_final['user_id'].map(user_mapper).astype(int)
user_info_final.drop('user_id', axis=1, inplace=True)

In [242]:
train_s['item_num'] = train_s['primary_video_id'].map(item_mapper).astype(int)
train_s['user_num'] = train_s['user_id'].map(user_mapper).astype(int)

In [230]:
rf = RandomForestClassifier(n_estimators=200, n_jobs=-1, random_state=11)
rf.fit(train_ss[train_feats].values, train_ss.target.values)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=200,
                       n_jobs=-1, oob_score=False, random_state=11, verbose=0,
                       warm_start=False)

In [247]:
n = len(hot_users)
result1 = pd.DataFrame([])

for i, u in enumerate(list(hot_users)):
    print(f'{i+1} user of {n}')
    u_map = user_mapper[u]
    pop_films_map = [item_mapper[x] for x in pop_films]

    tmp = pd.DataFrame([], columns=['user_num', 'item_num'])
    tmp['item_num'] = pop_films_map
    tmp['user_num'] = [u_map]*tmp.shape[0]

    tmp = tmp.merge(item_info_final, on='item_num')
    tmp = tmp.merge(user_info_final, on='user_num')
    tmp = tmp.merge(train_s[['user_num', 'item_num', 'week']], 
                    how='left', on=['user_num', 'item_num'])
    tmp = tmp[tmp['week'].isna()]
    tmp.drop('week', axis=1, inplace=True)

    prob = rf.predict_proba(tmp[train_feats].values)[:, 1]
    
    tmp['prob'] = prob
    tmp = tmp.sort_values('prob', ascending=False)
    result1 = result1.append(tmp[['user_num', 'item_num']].head(10))

1 user of 154522
2 user of 154522
3 user of 154522
4 user of 154522
5 user of 154522
6 user of 154522
7 user of 154522
8 user of 154522
9 user of 154522
10 user of 154522
11 user of 154522
12 user of 154522
13 user of 154522
14 user of 154522
15 user of 154522
16 user of 154522
17 user of 154522
18 user of 154522
19 user of 154522
20 user of 154522
21 user of 154522
22 user of 154522
23 user of 154522
24 user of 154522
25 user of 154522
26 user of 154522
27 user of 154522
28 user of 154522
29 user of 154522
30 user of 154522
31 user of 154522
32 user of 154522
33 user of 154522
34 user of 154522
35 user of 154522
36 user of 154522
37 user of 154522
38 user of 154522
39 user of 154522
40 user of 154522
41 user of 154522
42 user of 154522
43 user of 154522
44 user of 154522
45 user of 154522
46 user of 154522
47 user of 154522
48 user of 154522
49 user of 154522
50 user of 154522
51 user of 154522
52 user of 154522
53 user of 154522
54 user of 154522
55 user of 154522
56 user of 154522
5

438 user of 154522
439 user of 154522
440 user of 154522
441 user of 154522
442 user of 154522
443 user of 154522
444 user of 154522
445 user of 154522
446 user of 154522
447 user of 154522
448 user of 154522
449 user of 154522
450 user of 154522
451 user of 154522
452 user of 154522
453 user of 154522
454 user of 154522
455 user of 154522
456 user of 154522
457 user of 154522
458 user of 154522
459 user of 154522
460 user of 154522
461 user of 154522
462 user of 154522
463 user of 154522
464 user of 154522
465 user of 154522
466 user of 154522
467 user of 154522
468 user of 154522
469 user of 154522
470 user of 154522
471 user of 154522
472 user of 154522
473 user of 154522
474 user of 154522
475 user of 154522
476 user of 154522
477 user of 154522
478 user of 154522
479 user of 154522
480 user of 154522
481 user of 154522
482 user of 154522
483 user of 154522
484 user of 154522
485 user of 154522
486 user of 154522
487 user of 154522
488 user of 154522
489 user of 154522
490 user of 

870 user of 154522
871 user of 154522
872 user of 154522
873 user of 154522
874 user of 154522
875 user of 154522
876 user of 154522
877 user of 154522
878 user of 154522
879 user of 154522
880 user of 154522
881 user of 154522
882 user of 154522
883 user of 154522
884 user of 154522
885 user of 154522
886 user of 154522
887 user of 154522
888 user of 154522
889 user of 154522
890 user of 154522
891 user of 154522
892 user of 154522
893 user of 154522
894 user of 154522
895 user of 154522
896 user of 154522
897 user of 154522
898 user of 154522
899 user of 154522
900 user of 154522
901 user of 154522
902 user of 154522
903 user of 154522
904 user of 154522
905 user of 154522
906 user of 154522
907 user of 154522
908 user of 154522
909 user of 154522
910 user of 154522
911 user of 154522
912 user of 154522
913 user of 154522
914 user of 154522
915 user of 154522
916 user of 154522
917 user of 154522
918 user of 154522
919 user of 154522
920 user of 154522
921 user of 154522
922 user of 

1287 user of 154522
1288 user of 154522
1289 user of 154522
1290 user of 154522
1291 user of 154522
1292 user of 154522
1293 user of 154522
1294 user of 154522
1295 user of 154522
1296 user of 154522
1297 user of 154522
1298 user of 154522
1299 user of 154522
1300 user of 154522
1301 user of 154522
1302 user of 154522
1303 user of 154522
1304 user of 154522
1305 user of 154522
1306 user of 154522
1307 user of 154522
1308 user of 154522
1309 user of 154522
1310 user of 154522
1311 user of 154522
1312 user of 154522
1313 user of 154522
1314 user of 154522
1315 user of 154522
1316 user of 154522
1317 user of 154522
1318 user of 154522
1319 user of 154522
1320 user of 154522
1321 user of 154522
1322 user of 154522
1323 user of 154522
1324 user of 154522
1325 user of 154522
1326 user of 154522
1327 user of 154522
1328 user of 154522
1329 user of 154522
1330 user of 154522
1331 user of 154522
1332 user of 154522
1333 user of 154522
1334 user of 154522
1335 user of 154522
1336 user of 154522


1697 user of 154522
1698 user of 154522
1699 user of 154522
1700 user of 154522
1701 user of 154522
1702 user of 154522
1703 user of 154522
1704 user of 154522
1705 user of 154522
1706 user of 154522
1707 user of 154522
1708 user of 154522
1709 user of 154522
1710 user of 154522
1711 user of 154522
1712 user of 154522
1713 user of 154522
1714 user of 154522
1715 user of 154522
1716 user of 154522
1717 user of 154522
1718 user of 154522
1719 user of 154522
1720 user of 154522
1721 user of 154522
1722 user of 154522
1723 user of 154522
1724 user of 154522
1725 user of 154522
1726 user of 154522
1727 user of 154522
1728 user of 154522
1729 user of 154522
1730 user of 154522
1731 user of 154522
1732 user of 154522
1733 user of 154522
1734 user of 154522
1735 user of 154522
1736 user of 154522
1737 user of 154522
1738 user of 154522
1739 user of 154522
1740 user of 154522
1741 user of 154522
1742 user of 154522
1743 user of 154522
1744 user of 154522
1745 user of 154522
1746 user of 154522


...

152806 user of 154522
152807 user of 154522
152808 user of 154522
152809 user of 154522
152810 user of 154522
152811 user of 154522
152812 user of 154522
152813 user of 154522
152814 user of 154522
152815 user of 154522
152816 user of 154522
152817 user of 154522
152818 user of 154522
152819 user of 154522
152820 user of 154522
152821 user of 154522
152822 user of 154522
152823 user of 154522
152824 user of 154522
152825 user of 154522
152826 user of 154522
152827 user of 154522
152828 user of 154522
152829 user of 154522
152830 user of 154522
152831 user of 154522
152832 user of 154522
152833 user of 154522
152834 user of 154522
152835 user of 154522
152836 user of 154522
152837 user of 154522
152838 user of 154522
152839 user of 154522
152840 user of 154522
152841 user of 154522
152842 user of 154522
152843 user of 154522
152844 user of 154522
152845 user of 154522
152846 user of 154522
152847 user of 154522
152848 user of 154522
152849 user of 154522
152850 user of 154522
152851 use

153179 user of 154522
153180 user of 154522
153181 user of 154522
153182 user of 154522
153183 user of 154522
153184 user of 154522
153185 user of 154522
153186 user of 154522
153187 user of 154522
153188 user of 154522
153189 user of 154522
153190 user of 154522
153191 user of 154522
153192 user of 154522
153193 user of 154522
153194 user of 154522
153195 user of 154522
153196 user of 154522
153197 user of 154522
153198 user of 154522
153199 user of 154522
153200 user of 154522
153201 user of 154522
153202 user of 154522
153203 user of 154522
153204 user of 154522
153205 user of 154522
153206 user of 154522
153207 user of 154522
153208 user of 154522
153209 user of 154522
153210 user of 154522
153211 user of 154522
153212 user of 154522
153213 user of 154522
153214 user of 154522
153215 user of 154522
153216 user of 154522
153217 user of 154522
153218 user of 154522
153219 user of 154522
153220 user of 154522
153221 user of 154522
153222 user of 154522
153223 user of 154522
153224 use

153552 user of 154522
153553 user of 154522
153554 user of 154522
153555 user of 154522
153556 user of 154522
153557 user of 154522
153558 user of 154522
153559 user of 154522
153560 user of 154522
153561 user of 154522
153562 user of 154522
153563 user of 154522
153564 user of 154522
153565 user of 154522
153566 user of 154522
153567 user of 154522
153568 user of 154522
153569 user of 154522
153570 user of 154522
153571 user of 154522
153572 user of 154522
153573 user of 154522
153574 user of 154522
153575 user of 154522
153576 user of 154522
153577 user of 154522
153578 user of 154522
153579 user of 154522
153580 user of 154522
153581 user of 154522
153582 user of 154522
153583 user of 154522
153584 user of 154522
153585 user of 154522
153586 user of 154522
153587 user of 154522
153588 user of 154522
153589 user of 154522
153590 user of 154522
153591 user of 154522
153592 user of 154522
153593 user of 154522
153594 user of 154522
153595 user of 154522
153596 user of 154522
153597 use

153925 user of 154522
153926 user of 154522
153927 user of 154522
153928 user of 154522
153929 user of 154522
153930 user of 154522
153931 user of 154522
153932 user of 154522
153933 user of 154522
153934 user of 154522
153935 user of 154522
153936 user of 154522
153937 user of 154522
153938 user of 154522
153939 user of 154522
153940 user of 154522
153941 user of 154522
153942 user of 154522
153943 user of 154522
153944 user of 154522
153945 user of 154522
153946 user of 154522
153947 user of 154522
153948 user of 154522
153949 user of 154522
153950 user of 154522
153951 user of 154522
153952 user of 154522
153953 user of 154522
153954 user of 154522
153955 user of 154522
153956 user of 154522
153957 user of 154522
153958 user of 154522
153959 user of 154522
153960 user of 154522
153961 user of 154522
153962 user of 154522
153963 user of 154522
153964 user of 154522
153965 user of 154522
153966 user of 154522
153967 user of 154522
153968 user of 154522
153969 user of 154522
153970 use

154298 user of 154522
154299 user of 154522
154300 user of 154522
154301 user of 154522
154302 user of 154522
154303 user of 154522
154304 user of 154522
154305 user of 154522
154306 user of 154522
154307 user of 154522
154308 user of 154522
154309 user of 154522
154310 user of 154522
154311 user of 154522
154312 user of 154522
154313 user of 154522
154314 user of 154522
154315 user of 154522
154316 user of 154522
154317 user of 154522
154318 user of 154522
154319 user of 154522
154320 user of 154522
154321 user of 154522
154322 user of 154522
154323 user of 154522
154324 user of 154522
154325 user of 154522
154326 user of 154522
154327 user of 154522
154328 user of 154522
154329 user of 154522
154330 user of 154522
154331 user of 154522
154332 user of 154522
154333 user of 154522
154334 user of 154522
154335 user of 154522
154336 user of 154522
154337 user of 154522
154338 user of 154522
154339 user of 154522
154340 user of 154522
154341 user of 154522
154342 user of 154522
154343 use

In [248]:
result1.to_csv('/data/agoryach/datagym-recsys-01/big-hw-02/output/golden_result.csv', index=False)

In [251]:
result1['user_id'] = result1['user_num'].map(user_mapper_rev)
result1['primary_video_id'] = result1['item_num'].map(item_mapper_rev)

In [253]:
result1.user_id.nunique()

154522

In [260]:
result1_agg = result1[['user_id', 'primary_video_id']].groupby('user_id')['primary_video_id'].apply(list).reset_index()

In [261]:
result1_agg['primary_video_id'] = result1_agg['primary_video_id'].apply(lambda x: ' '.join([str(a) for a in x]))

### join results

In [264]:
result = pd.concat((result1_agg, result2))

In [265]:
result.to_csv('/data/agoryach/datagym-recsys-01/big-hw-02/output/submission_6.csv', index=False)

In [ ]:
#hot_test = test[test['user_id'].isin(hot_users)]
# hot_test['primary_video_id_list'] = pd.Series([pop_films]*hot_test.shape[0])
# hot_test.shape
# full_hot_test = hot_test.set_index('user_id').primary_video_id_list.explode().reset_index()\
# .rename(columns={'primary_video_id_list':'primary_video_id'})
# full_hot_test = full_hot_test.merge(train_s[['user_id', 'primary_video_id', 'week']], 
#                                     how='left', on=['user_id', 'primary_video_id'])
# full_hot_test.shape
# full_hot_test = full_hot_test[full_hot_test['week'].isna()]
# full_hot_test.shape
# full_hot_test.drop('week', axis=1, inplace=True)